# Projeto Machine Learning

[Explicação do projeto]

[Motivação]

[Índice]

# Importando Libs

In [1]:
# Libs matplotlib, numpy and pandas
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

# Lib librosa
import librosa
import librosa.display

# Lib OS
from os import listdir
from os.path import isfile, join, exists

# Lib ipwidgets
from ipywidgets import interact, IntSlider, interact_manual

# Lib IPtyhon Display
import IPython.display as ipd

# Lib glob
import glob

# Lib sklearn
from sklearn import svm

# Carregando Dataset

Baixar todo o [dataset](https://www.kaggle.com/carlthome/gtzan-genre-collection) (genre/) e colocar na mesma pasta do projeto.

In [2]:
def import_signal(path):
    
    # Test if path exists
    if( exists(path) == False ):
        print("Path does not exist, download from https://www.kaggle.com/carlthome/gtzan-genre-collection")
        return 0, 0
    
    # Load files woth glob
    files = glob.glob(path + '*.au')
    audios = []
    
    # Load audio files with sample rate 22050 Hz
    for file in files: 
        s, sr = librosa.core.load(file, sr=22050)
        audios.append(s)
        
    # Return audio vector and sample rate
    return audios, sr

## Estilo Popular (nº 0)

In [3]:
# Import Popular audio files
pop_audios, pop_sr = import_signal('genres/pop/')

pop_audios_df = pd.DataFrame([[x] for x in pop_audios], columns=['x'])
pop_audios_df['y'] = 0
pop_audios_df['y2'] = 0
#pop_audios_df.head()

In [5]:
# Por algum motivo o interact não funciona com o ipd.Audio

# @interact(x=IntSlider(min=0, max=99, step=1, value=0))
# def _f(x):
#     ipd.Audio(pop_audios[x], rate=pop_sr)
    
x = 23
ipd.Audio(pop_audios[x], rate=pop_sr)

## Estilo Clássico (nº 1)

In [7]:
# Import Classical audio files
classical_audios, classical_sr = import_signal('genres/classical/')

classical_audios_df = pd.DataFrame([[x] for x in classical_audios], columns=['x'])
classical_audios_df['y'] = 1
classical_audios_df['y2'] = 0
#classical_audios_df.head()

In [8]:
# Por algum motivo o interact não funciona com o ipd.Audio

# @interact(x=IntSlider(min=0, max=99, step=1, value=0))
# def _f(x):
#     ipd.Audio(classical_audios[x], rate=classical_sr)
    
x = 24
ipd.Audio(classical_audios[x], rate=classical_sr)

## Estilo Jazz (nº 2)

In [9]:
# Import Jazz audio files
jazz_audios, jazz_sr = import_signal('genres/jazz/')

jazz_audios_df = pd.DataFrame([[x] for x in jazz_audios], columns=['x'])
jazz_audios_df['y'] = 2
jazz_audios_df['y2'] = 1
#jazz_audios_df.head()

In [10]:
# Por algum motivo o interact não funciona com o ipd.Audio

# @interact(x=IntSlider(min=0, max=99, step=1, value=0))
# def _f(x):
#     ipd.Audio(jazz_audios[x], rate=jazz_sr)
    
x = 35
ipd.Audio(jazz_audios[x], rate=jazz_sr)

## Estilo Rock (n º3)

In [11]:
# Import Rock audio files
rock_audios, rock_sr = import_signal('genres/rock/')

rock_audios_df = pd.DataFrame([[x] for x in rock_audios], columns=['x'])
rock_audios_df['y'] = 3
rock_audios_df['y2'] = 1
#rock_audios_df.head()

In [12]:
# Por algum motivo o interact não funciona com o ipd.Audio

# @interact(x=IntSlider(min=0, max=99, step=1, value=0))
# def _f(x):
#     ipd.Audio(rock_audios[x], rate=rock_sr)
    
x = 3
ipd.Audio(rock_audios[x], rate=rock_sr)

## Verificando os Sample Rates

In [13]:
pop_sr == classical_sr == jazz_sr == rock_sr

True

In [14]:
sr = pop_sr
sr

22050

## Criando vertor de audios

In [15]:
audios = (
    pd.concat([ pop_audios_df, 
                classical_audios_df, 
                jazz_audios_df, 
                rock_audios_df])
    .sample(frac=1)
    .reset_index(drop=True) #shuffle
)

print(f'Rows: {len(audios)}')
#audios.head()

Rows: 400


## Dividindo entre  Train e Test

In [16]:
# Splitting int train and test
msk = np.random.rand(len(audios)) < 0.8
train = audios[msk]
test = audios[~msk]

print(f'Rows train:{len(train)}')
print(f'Rows test:{len(test)}')

Rows train:323
Rows test:77


In [17]:
print("Train count Y axis:")
print(train.groupby('y').count())
print(" ")
print("Train count Y2 axis:")
print(train.groupby('y2').count())
print(" ")
print("Test count Y axis:")
print(test.groupby('y').count())
print(" ")
print("Test count Y2 axis:")
print(test.groupby('y2').count())

Train count Y axis:
    x  y2
y        
0  74  74
1  75  75
2  91  91
3  83  83
 
Train count Y2 axis:
      x    y
y2          
0   149  149
1   174  174
 
Test count Y axis:
    x  y2
y        
0  26  26
1  25  25
2   9   9
3  17  17
 
Test count Y2 axis:
     x   y
y2        
0   51  51
1   26  26


## Extração de Features

### MFCC

In [19]:
# Train
mfcc_list_train = []
for x in train['x']:
    mfcc = np.array(librosa.feature.mfcc(y=x, sr=sr)).flatten()
    zeros = np.zeros((26280 - len(mfcc)))
    mfcc_list_train.append(np.concatenate((mfcc, zeros), axis=0))
train['mfcc'] = mfcc_list_train

# Test
mfcc_list_test = []
for x in test['x']:
    mfcc = np.array(librosa.feature.mfcc(y=x, sr=sr)).flatten()
    zeros = np.zeros((26280 - len(mfcc)))
    mfcc_list_test.append(np.concatenate((mfcc, zeros), axis=0))
test['mfcc'] = mfcc_list_test

# Results
train.head()
test.head()

<ipython-input-19-3a1984b64ed8>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['mfcc'] = mfcc_list_train
<ipython-input-19-3a1984b64ed8>:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['mfcc'] = mfcc_list_test


x  y  y2  \
4   [-0.09780884, -0.09225464, 0.009094238, 0.0249...  3   1   
13  [-0.021331787, -0.031280518, -0.0368042, -0.03...  1   0   
14  [0.03201294, 0.042877197, 0.049102783, 0.05834...  0   0   
26  [-0.06484985, -0.10720825, -0.109436035, -0.09...  1   0   
29  [0.007873535, 0.005279541, 0.004486084, 0.0036...  1   0   

                                                 mfcc  
4   [-60.82146453857422, -68.71263122558594, -79.4...  
13  [-276.8092041015625, -290.64971923828125, -315...  
14  [-72.08540344238281, 36.97532653808594, 62.247...  
26  [-111.6563720703125, -111.31787109375, -120.01...  
29  [-383.77313232421875, -396.5204772949219, -430...

### LPC

In [20]:
# Train
lpc_list = []
for x in train['x']:
    lpc = librosa.lpc(x, 6)
    lpc_list.append(lpc)
train['lpc'] = lpc_list

# Test
lpc_list = []
for x in test['x']:
    lpc = librosa.lpc(x, 6)
    lpc_list.append(lpc)    
test['lpc'] = lpc_list

# Results
test.head()
train.head()

<ipython-input-20-0e4594c6b305>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['lpc'] = lpc_list
<ipython-input-20-0e4594c6b305>:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['lpc'] = lpc_list


x  y  y2  \
0  [-0.018615723, -0.022918701, -0.0064697266, -0...  2   1   
1  [-0.025543213, -0.071777344, -0.11016846, -0.1...  2   1   
2  [0.012359619, -0.0107421875, -0.03161621, -0.0...  0   0   
3  [0.17285156, 0.16674805, 0.16027832, 0.1631164...  3   1   
5  [-0.029846191, -0.054779053, -0.06448364, -0.0...  0   0   

                                                mfcc  \
0  [-109.0660629272461, -85.43883514404297, -53.3...   
1  [-100.41613006591797, -120.69935607910156, -16...   
2  [-77.66487884521484, -12.498249053955078, -3.3...   
3  [-204.85328674316406, -212.54959106445312, -23...   
5  [-130.87130737304688, -123.27816772460938, -13...   

                                                 lpc  
0  [1.0, -1.3200337, 0.3858651, 0.15471873, -0.09...  
1  [1.0, -2.404841, 2.7243788, -2.2495322, 1.7738...  
2  [1.0, -0.23227462, -0.3959549, -0.16198325, -0...  
3  [1.0, -0.7622068, -0.34360754, -0.10448362, 0....  
5  [1.0, -0.48145485, -0.45947364, -0.2426259, 0....

## Cenário I

* Usando uma rede SVM de apenas uma cama para reconhecer os 4 tipos musicais

### Plot functions

In [ ]:
# pesquisar

### MFCC

Descrição da feature

In [21]:
# Training
model_mfcc = svm.SVC()
model_mfcc.fit(train['mfcc'].to_list(), train['y'].to_list())

SVC()

In [22]:
# Results
print('Train accuracy: {:.1%}'.format(model_mfcc.score(train['mfcc'].to_list(), train['y'].to_list())))
print('Test accuracy: {:.1%}'.format(model_mfcc.score(test['mfcc'].to_list(), test['y'].to_list())))

Train accuracy: 79.6%
Test accuracy: 80.5%


### Conclusão

### LPC

Descrição da feature

In [23]:
# Training
model_lpc = svm.SVC()
model_lpc.fit(train['lpc'].to_list(), train['y'].to_list())

SVC()

In [24]:
# Results
print('Train accuracy: {:.1%}'.format(model_lpc.score(train['lpc'].to_list(), train['y'].to_list())))
print('Test accuracy: {:.1%}'.format(model_lpc.score(test['lpc'].to_list(), test['y'].to_list())))

Train accuracy: 66.6%
Test accuracy: 76.6%


### Conclusão

### MFCC & LPC

Descrição da junção das duas

### Conclusão

## Cenário II

* Usando 3 redes SVM (NECESSITA DESCRIçÃO)

In [25]:
def second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='mfcc'):
    # SVM1
    model1 = svm.SVC()
    model1.fit(train[f'{feature_ex_svm1}'].to_list(), train['y2'].to_list())
    train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())
    
    #SVM2
    train_2 = train[train['y2_predicted']==0]
    train_2 = train_2[train_2['y'].isin([0,1])]
    test_2 = test[test['y2']==0]
    model2 = svm.SVC()
    model2.fit(train_2[f'{feature_ex_svm23}'].to_list(), train_2['y'].to_list())
    
    #SVM3
    train_3 = train[train['y2_predicted']==1]
    train_3 = train_3[train_3['y'].isin([2,3])]
    test_3 = test[test['y2']==1]
    model3 = svm.SVC()
    model3.fit(train_3[f'{feature_ex_svm23}'].to_list(), train_3['y'].to_list())
    
    train_score = (
        model2.score(train_2[f'{feature_ex_svm23}'].to_list(), train_2['y'].to_list()) * 0.5 +
        model3.score(train_3[f'{feature_ex_svm23}'].to_list(), train_3['y'].to_list()) * 0.5
    )
    
    test_score = (
        model2.score(test_2[f'{feature_ex_svm23}'].to_list(), test_2['y'].to_list()) * 0.5 +
        model3.score(test_3[f'{feature_ex_svm23}'].to_list(), test_3['y'].to_list()) * 0.5
    )
    
    print('Train accuracy: {:.1%}'.format(train_score))
    print('Test accuracy: {:.1%}'.format(test_score))

In [26]:
second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='mfcc')

<ipython-input-25-75b3c33804b3>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())


Train accuracy: 93.9%
Test accuracy: 91.3%


In [27]:
second_scenario_classification(train, test, feature_ex_svm1='lpc', feature_ex_svm23='lpc')

Train accuracy: 84.0%
Test accuracy: 85.5%


<ipython-input-25-75b3c33804b3>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())


In [28]:
second_scenario_classification(train, test, feature_ex_svm1='mfcc', feature_ex_svm23='mfcc')

<ipython-input-25-75b3c33804b3>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())


Train accuracy: 92.8%
Test accuracy: 91.3%


In [29]:
second_scenario_classification(train, test, feature_ex_svm1='mfcc', feature_ex_svm23='lpc')

Train accuracy: 88.6%
Test accuracy: 79.8%


<ipython-input-25-75b3c33804b3>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['y2_predicted'] = model1.predict(train[f'{feature_ex_svm1}'].to_list())


### Conclusão

## Teste com algum audio